# Tutorial 51: Dataframes_SIR3S_Model 

This Example demonstrates the capabilities of the class Dataframes_SIR3S_Model that extends SIR3S_Model be abilities to work directley with pandas dataframes.  

# Toolkit Release

In [1]:
#pip install 

# Imports

## SIR 3S Toolkit

### Regular Import/Init

In [2]:
SIR3S_SIRGRAF_DIR = r"C:\3S\SIR 3S Entwicklung\SirGraf-90-15-00-19_x64" #change to local path

In [3]:
from sir3stoolkit.core import wrapper

In [4]:
wrapper

<module 'sir3stoolkit.core.wrapper' from 'C:\\Users\\aUsername\\3S\\sir3stoolkit\\src\\sir3stoolkit\\core\\wrapper.py'>

In [5]:
wrapper.Initialize_Toolkit(SIR3S_SIRGRAF_DIR)

### Additional Import/Init for Dataframes class

In [6]:
from sir3stoolkit.mantle.dataframes import SIR3S_Model_Dataframes

In [7]:
s3s = SIR3S_Model_Dataframes()

Initialization complete


## Additional

In [8]:
import pandas as pd
from shapely.geometry import Point
import re
import folium
from folium.plugins import HeatMap
import numpy as np
import geopandas as gpd
from shapely import wkt
import matplotlib.pyplot as plt
import contextily as cx

# Open Model

In [9]:
s3s.OpenModel(dbName=r"C:\Users\aUsername\3S\PT3S\PT3S\Examples\Example3.db3",
              providerType=s3s.ProviderTypes.SQLite,
              Mid="M-1-0-1",
              saveCurrentlyOpenModel=False,
              namedInstance="",
              userID="",
              password="")

Model is open for further operation


# Manual Dataframe creation

## Metadata - Nodes

We can use the [generate_element_metadata_dataframe()](https://3sconsult.github.io/sir3stoolkit/references/sir3stoolkit.mantle.html#sir3stoolkit.mantle.dataframes.Dataframes_SIR3S_Model.generate_element_metadata_dataframe) method to obtain a dataframe for all instances of a specifc component type (Nodes, Pipes, etc.) with user defined metadata properties (all non-result data related to a component) to be added. For this example we will use nodes.

In this case we are interested in Nodes, let's check what metadata properties are available for this element.

In [10]:
s3s.GetPropertiesofElementType(s3s.ObjectTypes.Node)

['Name',
 'Ktyp',
 'Zkor',
 'QmEin',
 'Lfakt',
 'Fkpzon',
 'Fkfstf',
 'Fkutmp',
 'Fkfqps',
 'Fkcont',
 'Fk2lknot',
 'Beschreibung',
 'Idreferenz',
 'Iplanung',
 'Kvr',
 'Qakt',
 'Xkor',
 'Ykor',
 'NodeNamePosition',
 'ShowNodeName',
 'KvrKlartext',
 'NumberOfVERB',
 'HasBlockConnection',
 'Tk',
 'Pk',
 'IsMarked',
 'InVariant',
 'GeometriesDiffer',
 'SymbolFactor',
 'bz.Drakonz',
 'bz.Fk',
 'bz.Fkpvar',
 'bz.Fkqvar',
 'bz.Fklfkt',
 'bz.PhEin',
 'bz.Tm',
 'bz.Te',
 'bz.PhMin']

In the below subcases differnt choices of parameters for creating the metadata dataframe manually are shown. Note that not all possible combination of paramters are shown here.

### Subcase 1: Minimal

Let's say for now we only want a dataframe with all node tks without any related data.

In [11]:
(s3s.generate_element_metadata_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=[]
                                        )).head(3)

[2025-12-05 20:20:45,646] INFO in sir3stoolkit.mantle.dataframes: [metadata] Generating metadata dataframe for element type: ObjectTypes.Node
[2025-12-05 20:20:45,657] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:45,660] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:45,682] INFO in sir3stoolkit.mantle.dataframes: [Resolving Metadata Properties] Using 0 metadata properties.
[2025-12-05 20:20:45,683] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieving ...
[2025-12-05 20:20:45,687] INFO in sir3stoolkit.mantle.dataframes: [metadata] Done. Shape: (517, 1)


tk
0  5669301360686511351
1  5397948523091900401
2  5239335112004772156

### Subcase 2: Specific Properties 

Let's say we now want the minimal dataframe extended with supply/return info (kvr) and height (Zkor) of the nodes.

In [12]:
(s3s.generate_element_metadata_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=["Kvr", "Zkor"]
                                        )).head(3)

[2025-12-05 20:20:45,721] INFO in sir3stoolkit.mantle.dataframes: [metadata] Generating metadata dataframe for element type: ObjectTypes.Node
[2025-12-05 20:20:45,725] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:45,730] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:45,733] INFO in sir3stoolkit.mantle.dataframes: [Resolving Metadata Properties] Using 2 metadata properties.
[2025-12-05 20:20:45,735] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieving metadata properties ['Kvr', 'Zkor']...
[2025-12-05 20:20:45,823] INFO in sir3stoolkit.mantle.dataframes: [metadata] Done. Shape: (517, 3)


tk Kvr    Zkor
0  5669301360686511351   1  554,04
1  5397948523091900401   1  556,16
2  5239335112004772156   1  561,01

### Subcase 3: Maximal

Let's say now we want basically all available metadata (non-result data) related to nodes. 

If geometry=True, the 2D Point geometry will be added for Nodes and it will be attempted to transform the DataFrame into a GeoDataFrame using the SRID (eg. EPSG: 25832) defined in the model. If no SRID is defined, the DataFrame will remain as a DataFrame, but the geometry column with be added nonetheless.

In [13]:
(s3s.generate_element_metadata_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=None # Instead of an empty or filled list, we pass None to indicate we want all available properties
                                        ,geometry=True # geometry data has to be explicitly requested
                                        )).head(3)

[2025-12-05 20:20:45,856] INFO in sir3stoolkit.mantle.dataframes: [metadata] Generating metadata dataframe for element type: ObjectTypes.Node
[2025-12-05 20:20:45,861] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:45,866] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:45,869] INFO in sir3stoolkit.mantle.dataframes: [Resolving Metadata Properties] No properties given → using ALL metadata properties for ObjectTypes.Node.
[2025-12-05 20:20:45,871] INFO in sir3stoolkit.mantle.dataframes: [Resolving Metadata Properties] Using 38 metadata properties.
[2025-12-05 20:20:45,873] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieving metadata properties ['Name', 'Ktyp', 'Zkor', 'QmEin', 'Lfakt', 'Fkpzon', 'Fkfstf', 'Fkutmp', 'Fkfqps', 'Fkcont', 'Fk2lknot', 'Beschreibung', 'Idreferenz', 'Iplanung', 'Kvr', 'Qakt', 'Xkor', 'Yk

tk    Name  Ktyp    Zkor QmEin Lfakt               Fkpzon  \
0  5669301360686511351  V-K03S  QKON  554,04     0     1  5520728169779652386   
1  5397948523091900401  V-K13S  QKON  556,16     0     1  5520728169779652386   
2  5239335112004772156  V-K23S  QKON  561,01     0     1  5520728169779652386   

                Fkfstf               Fkutmp Fkfqps               Fkcont  \
0  4798673252636751115  5591325053703727727     -1  5029128874972463118   
1  4798673252636751115  5591325053703727727     -1  5029128874972463118   
2  4798673252636751115  5591325053703727727     -1  5029128874972463118   

              Fk2lknot                       Beschreibung  \
0  5761544923588724980                Abzw. Am Sonnenbühl   
1  4749864932928780363  Anfangsknoten generiert von SirDB   
2  4899862460906451371  Anfangsknoten generiert von SirDB   

                           Idreferenz Iplanung Kvr Qakt              Xkor  \
0  3S3768E2953006F125B34916F6A1681667        1   1    0  713620,267807079   
1  3SC30ED954AA2F1D59B1F92FFEBCCB7B5B        1   1    0  713602,294599536   
2  3SC30ED954AA2F1D59B1F92FFEBCCB7B5B        1   1    0  713574,061626605   

               Ykor NodeNamePosition ShowNodeName KvrKlartext NumberOfVERB  \
0  5578828,41875394                1        False     Vorlauf            0   
1  5578860,10567987                1        False     Vorlauf            0   
2  5578909,87290685                1        False     Vorlauf            0   

  HasBlockConnection                   Tk                   Pk IsMarked  \
0              False  5669301360686511351  5669301360686511351    False   
1              False  5397948523091900401  5397948523091900401    False   
2              False  5239335112004772156  5239335112004772156    False   

  InVariant GeometriesDiffer SymbolFactor bz.Drakonz                bz.Fk  \
0     False            False          0,2          0  5669301360686511351   
1     False            False          0,2          0  5397948523091900401   
2     False            False          0,2          0  5239335112004772156   

  bz.Fkpvar bz.Fkqvar bz.Fklfkt bz.PhEin bz.Tm bz.Te bz.PhMin  \
0        -1        -1        -1        0     0     0        0   
1        -1        -1        -1        0     0     0        0   
2        -1        -1        -1        0     0     0        0   

                         geometry  
0  POINT (713620.268 5578828.419)  
1  POINT (713602.295 5578860.106)  
2  POINT (713574.062 5578909.873)

### Subcase 4: Container Filtering + Element Type Col

Let's say we only want nodes inside a specific container and we also want to have an element type col adding "Node" to each row (useful when joining with other dataframes later).

In [14]:
for container_id in (s3s.GetTksofElementType(s3s.ObjectTypes.ObjectContainerSymbol)):
    print(f"{container_id}: {s3s.GetValue(container_id, 'Name')[0]}")

5029128874972463118: M-1-0-1
5027846505677995694: Erzeugung
5172832702839270493: TS
5152808213068069018: Laststeuerung
5467315850619588583: Sekundärwerte
5320319133990336755: Netztrennung


If we filter for a container with no nodes, we will run into an error.

In [15]:
s3s.generate_element_metadata_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=["Kvr", "Zkor"]
                                        ,geometry=True
                                        ,filter_container_tks=["5152808213068069018"]
                                        ,element_type_col=True
                                        )

[2025-12-05 20:20:49,525] INFO in sir3stoolkit.mantle.dataframes: [metadata] Generating metadata dataframe for element type: ObjectTypes.Node
[2025-12-05 20:20:49,535] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:49,540] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:49,592] ERROR in sir3stoolkit.mantle.dataframes: [Resolving tks] No elements remain after container filtering.


pandas.core.frame.DataFrame

But if we add the main container id to the list, we will find nodes.

In [16]:
(s3s.generate_element_metadata_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=[]
                                        ,geometry=True
                                        ,filter_container_tks=["5029128874972463118", "5152808213068069018"]
                                        ,element_type_col=True
                                        )).head(3)

[2025-12-05 20:20:49,619] INFO in sir3stoolkit.mantle.dataframes: [metadata] Generating metadata dataframe for element type: ObjectTypes.Node
[2025-12-05 20:20:49,624] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:49,628] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:49,671] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] 500 tks remain after container filtering.
[2025-12-05 20:20:49,675] INFO in sir3stoolkit.mantle.dataframes: [Resolving Metadata Properties] Using 0 metadata properties.
[2025-12-05 20:20:49,678] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieving geometry...
[2025-12-05 20:20:49,818] INFO in sir3stoolkit.mantle.dataframes: [metadata] Transforming DataFrame to GeoDataFrame successful with EPSG: 25832
[2025-12-05 20:20:49,821] INFO in sir3stoolkit.mantle.dataframes: [metadata] Done. Sha

tk                        geometry element type
0  5669301360686511351  POINT (713620.268 5578828.419)         Node
1  5397948523091900401  POINT (713602.295 5578860.106)         Node
2  5239335112004772156  POINT (713574.062 5578909.873)         Node

### Subcase 5: Non-Container Filtering

If we want to filter for more than just the container, we have to filter tks outside the function and then pass them.

In [17]:
all_tks = s3s.GetTksofElementType(s3s.ObjectTypes.Node)

In [18]:
len(all_tks)

517

In [19]:
good_tks = []

In [20]:
for tk in all_tks:
    if s3s.GetValue(tk, "Kvr")[0] == "1": # Supply/Vorlauf
        good_tks.append(tk)

In [21]:
len(good_tks)

256

In [22]:
(s3s.generate_element_metadata_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,tks=good_tks
                                        ,properties=[]
                                        ,geometry=True
                                        )).head(3)

[2025-12-05 20:20:50,101] INFO in sir3stoolkit.mantle.dataframes: [metadata] Generating metadata dataframe for element type: ObjectTypes.Node
[2025-12-05 20:20:50,107] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:50,113] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2025-12-05 20:20:50,119] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] 256 tks remain after filtering for given tks.
[2025-12-05 20:20:50,125] INFO in sir3stoolkit.mantle.dataframes: [Resolving Metadata Properties] Using 0 metadata properties.
[2025-12-05 20:20:50,127] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieving geometry...
[2025-12-05 20:20:50,299] INFO in sir3stoolkit.mantle.dataframes: [metadata] Transforming DataFrame to GeoDataFrame successful with EPSG: 25832
[2025-12-05 20:20:50,301] INFO in sir3stoolkit.mantle.dataframes: [metadata] Done.

tk                        geometry
0  5669301360686511351  POINT (713620.268 5578828.419)
1  5397948523091900401  POINT (713602.295 5578860.106)
2  5239335112004772156  POINT (713574.062 5578909.873)

## Result Data - Pipes

We can use the [generate_element_metadata_dataframe()](https://3sconsult.github.io/sir3stoolkit/references/sir3stoolkit.mantle.html#sir3stoolkit.mantle.dataframes.Dataframes_SIR3S_Model.generate_element_results_dataframe) method to obtain a dataframe for all instances of a specifc component type (Nodes, Pipes, etc.) with user defined result values for certain timestamps to be added. For this example we will use pipes.

Let's check what result properties are available for Pipes.

In [23]:
s3s.GetResultProperties_from_elementType(elementType=s3s.ObjectTypes.Pipe
                                         ,onlySelectedVectors=False 
                                         )

['A',
 'ACALC',
 'CPI',
 'CPK',
 'DH',
 'DP',
 'DRAGRED',
 'DRAKONZ',
 'DSI',
 'DSK',
 'DTTR',
 'DWVERL',
 'DWVERLABS',
 'ETAAV',
 'FS',
 'HR',
 'HVEC',
 'IAKTIV',
 'IRTRENN',
 'JV',
 'JV2',
 'LAMBDA',
 'LECKEINAUS',
 'LECKMENGE',
 'LECKORT',
 'LINEPACK',
 'LINEPACKGEOM',
 'LINEPACKRATE',
 'MAINELEMENT',
 'MAV',
 'MI',
 'MK',
 'MKOND',
 'MMAX_INST',
 'MMIN_INST',
 'MVEC',
 'MVECMAX_INST',
 'MVECMIN_INST',
 'PAV',
 'PDAMPF',
 'PHR',
 'PHVEC',
 'PMAX',
 'PMIN',
 'PR',
 'PVEC',
 'PVECMAX_INST',
 'PVECMIN_INST',
 'QI2',
 'QK2',
 'QMAV',
 'QMI',
 'QMK',
 'QMMAX_INST',
 'QMMIN_INST',
 'QMVEC',
 'QSVB',
 'RHOAV',
 'RHOI',
 'RHOK',
 'RHOVEC',
 'SVEC',
 'TAV',
 'TI',
 'TK',
 'TTRVEC',
 'TVEC',
 'TVECMAX_INST',
 'TVECMIN_INST',
 'VAV',
 'VI',
 'VK',
 'VMAX_INST',
 'VMIN_INST',
 'VOLDA',
 'WALTERI',
 'WALTERK',
 'WVL',
 'ZAUS',
 'ZEIN',
 'ZHKNR',
 'ZVEC']

Let's also check what simulation timestamps are available in the model.

In [24]:
s3s.GetTimeStamps()[0] # list of simulation timestamps

['2023-02-13 00:00:00.000 +01:00',
 '2023-02-13 01:00:00.000 +01:00',
 '2023-02-13 02:00:00.000 +01:00',
 '2023-02-13 03:00:00.000 +01:00',
 '2023-02-13 04:00:00.000 +01:00',
 '2023-02-13 05:00:00.000 +01:00',
 '2023-02-13 06:00:00.000 +01:00',
 '2023-02-13 07:00:00.000 +01:00',
 '2023-02-13 08:00:00.000 +01:00',
 '2023-02-13 09:00:00.000 +01:00',
 '2023-02-13 10:00:00.000 +01:00',
 '2023-02-13 11:00:00.000 +01:00',
 '2023-02-13 12:00:00.000 +01:00',
 '2023-02-13 13:00:00.000 +01:00',
 '2023-02-13 14:00:00.000 +01:00',
 '2023-02-13 15:00:00.000 +01:00',
 '2023-02-13 16:00:00.000 +01:00',
 '2023-02-13 17:00:00.000 +01:00',
 '2023-02-13 18:00:00.000 +01:00',
 '2023-02-13 19:00:00.000 +01:00',
 '2023-02-13 20:00:00.000 +01:00',
 '2023-02-13 21:00:00.000 +01:00',
 '2023-02-13 22:00:00.000 +01:00',
 '2023-02-13 23:00:00.000 +01:00',
 '2023-02-14 00:00:00.000 +01:00']

In [25]:
s3s.GetTimeStamps()[1] # Static

'2023-02-13 00:00:00.000 +01:00'

In the below subcases differnt choices of parameters for creating the result dataframe manually are shown. Note that not all possible combination of paramters are shown here.

### Subcase 1: Static + All Result Values

In [26]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=None # None => All available properties
                                        ,timestamps=[s3s.GetTimeStamps()[1]] # static
                                        )).head(3)

[2025-12-05 20:20:51,296] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe


[2025-12-05 20:20:51,895] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] Only static timestamp 2023-02-13 00:00:00.000 +01:00 is used
[2025-12-05 20:20:51,895] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 1 valid timestamp(s) will be used.
[2025-12-05 20:20:51,906] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:20:51,913] INFO in sir3stoolkit.mantle.dataframes: [results] No properties given → using ALL non-vectorized result properties for ObjectTypes.Pipe.
[2025-12-05 20:20:51,917] INFO in sir3stoolkit.mantle.dataframes: [results] Using 66 result properties.
[2025-12-05 20:20:52,416] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result properties...
[2025-12-05 20:21:11,168] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (1, 34584)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                                A   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                                0.0           

tk                                                                           \
name                                                                          
end_nodes                                                                     
property                          ACALC      CPI      CPK       DH       DP   
timestamp                                                                     
2023-02-13 00:00:00.000 +01:00  99999.0  99999.0  99999.0  99999.0  99999.0   

tk                                                                            \
name                                                                           
end_nodes                                                                      
property                        DRAGRED  DRAKONZ      DSI      DSK      DTTR   
timestamp                                                                      
2023-02-13 00:00:00.000 +01:00  99999.0  99999.0  99999.0  99999.0  0.013437   

tk                                                                             \
name                                                                            
end_nodes                                                                       
property                          DWVERL DWVERLABS    ETAAV       FS       HR   
timestamp                                                                       
2023-02-13 00:00:00.000 +01:00  35.86027  1.306366  99999.0  99999.0  99999.0   

tk                                                                         \
name                                                                        
end_nodes                                                                   
property                       IAKTIV IRTRENN        JV      JV2   LAMBDA   
timestamp                                                                   
2023-02-13 00:00:00.000 +01:00    0.0     0.0  0.286071  99999.0  99999.0   

tk                                                                     \
name                                                                    
end_nodes                                                               
property                       LECKEINAUS LECKMENGE  LECKORT LINEPACK   
timestamp                                                               
2023-02-13 00:00:00.000 +01:00    99999.0   99999.0  99999.0  99999.0   

tk                                                                             \
name                                                                            
end_nodes                                                                       
property                       LINEPACKGEOM LINEPACKRATE MAINELEMENT      MAV   
timestamp                                                                       
2023-02-13 00:00:00.000 +01:00      99999.0      99999.0     99999.0  99999.0   

tk                                                                             \
name                                                                            
end_nodes                                                                       
property                             MI       MK    MKOND MMAX_INST MMIN_INST   
timestamp                                                                       
2023-02-13 00:00:00.000 +01:00  99999.0  99999.0  99999.0   99999.0   99999.0   

tk                                                                    \
name                                              

Note that a multi index on the columns is created, holding the most important metadata.
- Level 0: tk (device ID)
- Level 1: name (device name)
- Level 2: end_nodes (tuple of connected node IDs as string)
- Level 3: property (result name)

As can be seen a lot of 99999.0 placeholder values are inserted, because we attempt to access many result values that SIR Calc can calculate but are not requested for this model. Therefore using all available result properties(properties=None), is generally not recommended.

### Subcase 2: All Timestamps + Specific Values

In [27]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["DTTR", "PHR"] # Specify result properties of interest
                                        ,timestamps=None # None => All available simulation timestamps
                                        )).head(5)

[2025-12-05 20:21:12,097] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2025-12-05 20:21:12,098] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] No timestamps were given. Checking available simulation timestamps (SIR3S_Model.GetTimeStamps()[0]).
[2025-12-05 20:21:12,224] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 25 simulation timestamp(s) are available.
[2025-12-05 20:21:12,370] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 25 valid timestamp(s) will be used.
[2025-12-05 20:21:12,373] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:21:12,376] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2025-12-05 20:21:12,398] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result properties...
[2025-12-05 20:21:16,497] INFO in sir3stoolkit.mantle.datafram

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 01:00:00.000 +01:00                                           0.013283           
2023-02-13 02:00:00.000 +01:00                                           0.013074           
2023-02-13 03:00:00.000 +01:00                                           0.012422           
2023-02-13 04:00:00.000 +01:00                                           0.011118           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 01:00:00.000 +01:00  0.010654   
2023-02-13 02:00:00.000 +01:00  0.010982   
2023-02-13 03:00:00.000 +01:00  0.012116   
2023-02-13 04:00:00.000 +01:00  0.014996   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.025380           
2023-02-13 01:00:00.000 +01:00                                           0.025093           
2023-02-13 02:00:00.000 +01:00                                           0.024704           
2023-02-13 03:00:00.000 +01:00                                           0.023484           
2023-02-13 04:00:00.000 +01:00                                           0.021045           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 01:00:00.000 +01:00  0.014936   
2023-02-13 02:00:00.000 +01:00  0.015388   
2023-02-13 03:00:00.000 +01:00  0.016949   
2023-02-13 04:00:00.000 +01:00  0.020907   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 01:00:00.000 +01:00                                           0.017629           
2023-02-13 02:00:00.000 +01:00                                           0.017354           
2023-02-13 03:00:00.000 +01:00                                           0.016491           
2023-02-13 04:00:00.000 +01:00                                           0.014767           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 01:00:00.000 +01:00  0.011113   
2023-02-13 02:00:

### Subcase 3: Specific Timestamps + Specific Values

We can specify the list of timestamps to include either as a list of str timestamps ...

In [28]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=['2023-02-13 00:00:00.000 +01:00', '2023-02-13 05:00:00.000 +01:00', '2023-02-13 23:00:00.000 +01:00'] 
                                        )).head(3)

[2025-12-05 20:21:17,262] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2025-12-05 20:21:17,425] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2025-12-05 20:21:17,429] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:21:17,431] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2025-12-05 20:21:17,449] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result properties...
[2025-12-05 20:21:18,142] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 1048)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.008582           
2023-02-13 23:00:00.000 +01:00                                           0.012623           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.024733   
2023-02-13 23:00:00.000 +01:00  0.011749   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.025380           
2023-02-13 05:00:00.000 +01:00                                           0.016282           
2023-02-13 23:00:00.000 +01:00                                           0.023859           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.034238   
2023-02-13 23:00:00.000 +01:00  0.016444   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.011407           
2023-02-13 23:00:00.000 +01:00                                           0.016756           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.025622   
2023-02-13 23:00:00.000 +01:00  0.012244   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.001901           
2023-02-13 23:00:00.000 +01:00                         

... or as a list of int indices.

In [29]:
simulation_timestamps=s3s.GetTimeStamps()[0]

In [30]:
for idx, timestamp in enumerate(simulation_timestamps):
    print(idx, timestamp)

0 2023-02-13 00:00:00.000 +01:00
1 2023-02-13 01:00:00.000 +01:00
2 2023-02-13 02:00:00.000 +01:00
3 2023-02-13 03:00:00.000 +01:00
4 2023-02-13 04:00:00.000 +01:00
5 2023-02-13 05:00:00.000 +01:00
6 2023-02-13 06:00:00.000 +01:00
7 2023-02-13 07:00:00.000 +01:00
8 2023-02-13 08:00:00.000 +01:00
9 2023-02-13 09:00:00.000 +01:00
10 2023-02-13 10:00:00.000 +01:00
11 2023-02-13 11:00:00.000 +01:00
12 2023-02-13 12:00:00.000 +01:00
13 2023-02-13 13:00:00.000 +01:00
14 2023-02-13 14:00:00.000 +01:00
15 2023-02-13 15:00:00.000 +01:00
16 2023-02-13 16:00:00.000 +01:00
17 2023-02-13 17:00:00.000 +01:00
18 2023-02-13 18:00:00.000 +01:00
19 2023-02-13 19:00:00.000 +01:00
20 2023-02-13 20:00:00.000 +01:00
21 2023-02-13 21:00:00.000 +01:00
22 2023-02-13 22:00:00.000 +01:00
23 2023-02-13 23:00:00.000 +01:00
24 2023-02-14 00:00:00.000 +01:00


In [31]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=[0, 5, -2] 
                                        )).head(3)

[2025-12-05 20:21:19,132] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2025-12-05 20:21:19,288] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2025-12-05 20:21:19,291] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:21:19,294] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2025-12-05 20:21:19,330] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result properties...
[2025-12-05 20:21:19,945] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 1048)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.008582           
2023-02-13 23:00:00.000 +01:00                                           0.012623           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.024733   
2023-02-13 23:00:00.000 +01:00  0.011749   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.025380           
2023-02-13 05:00:00.000 +01:00                                           0.016282           
2023-02-13 23:00:00.000 +01:00                                           0.023859           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.034238   
2023-02-13 23:00:00.000 +01:00  0.016444   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.011407           
2023-02-13 23:00:00.000 +01:00                                           0.016756           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.025622   
2023-02-13 23:00:00.000 +01:00  0.012244   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.001901           
2023-02-13 23:00:00.000 +01:00                         

### Subcase 4: Specific Timestamps + Specific Values + Container Filtering

As for metadatat dataframes we can give a list of container tks to filter for.

In [32]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=[0, 5, -2] 
                                        ,filter_container_tks=[s3s.GetMainContainer()[0]]
                                        )).head(3)

[2025-12-05 20:21:20,790] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2025-12-05 20:21:20,868] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2025-12-05 20:21:20,871] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:21:20,910] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] 524 tks remain after container filtering.
[2025-12-05 20:21:20,913] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2025-12-05 20:21:20,929] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result properties...
[2025-12-05 20:21:21,616] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 1048)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.008582           
2023-02-13 23:00:00.000 +01:00                                           0.012623           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.024733   
2023-02-13 23:00:00.000 +01:00  0.011749   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.025380           
2023-02-13 05:00:00.000 +01:00                                           0.016282           
2023-02-13 23:00:00.000 +01:00                                           0.023859           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.034238   
2023-02-13 23:00:00.000 +01:00  0.016444   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.011407           
2023-02-13 23:00:00.000 +01:00                                           0.016756           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.025622   
2023-02-13 23:00:00.000 +01:00  0.012244   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.001901           
2023-02-13 23:00:00.000 +01:00                         

### Subcase 5: Specific Timestamps + Specific Values + Filtering

If we want to filter for more than just the container, we have to filter tks outside the function and then pass them. Works same way as for metadata.

In [33]:
all_tks = s3s.GetTksofElementType(s3s.ObjectTypes.Pipe)

In [34]:
len(all_tks)

524

In [35]:
good_tks = []

In [36]:
s3s.GetTksofElementType(s3s.ObjectTypes.PipeGroup) # Leitungsgruppe

['5109995988251362606', '4779752876656844188']

In [37]:
for tk in all_tks:
    if s3s.GetValue(tk, "Fkltgr")[0] == '4779752876656844188': # Leitungsgruppe
        if s3s.GetValue(tk, "bz.Irtrenn")[0] == "0": # Rohr nicht getrennt
            good_tks.append(tk)

In [38]:
len(good_tks)

480

In [39]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,tks=good_tks # here we specify that not all available tks should be used
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=[0, 5, -2] 
                                        ,filter_container_tks=[s3s.GetMainContainer()[0]]
                                        )).head(3)

[2025-12-05 20:21:22,644] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2025-12-05 20:21:22,732] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2025-12-05 20:21:22,734] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:21:22,738] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] 480 tks remain after filtering for given tks.
[2025-12-05 20:21:22,778] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] 480 tks remain after container filtering.
[2025-12-05 20:21:22,778] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2025-12-05 20:21:22,805] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result properties...
[2025-12-05 20:21:23,410] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 960)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.008582           
2023-02-13 23:00:00.000 +01:00                                           0.012623           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.024733   
2023-02-13 23:00:00.000 +01:00  0.011749   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.025380           
2023-02-13 05:00:00.000 +01:00                                           0.016282           
2023-02-13 23:00:00.000 +01:00                                           0.023859           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.034238   
2023-02-13 23:00:00.000 +01:00  0.016444   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.011407           
2023-02-13 23:00:00.000 +01:00                                           0.016756           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.025622   
2023-02-13 23:00:00.000 +01:00  0.012244   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.001901           
2023-02-13 23:00:00.000 +01:00                         

### Subcase 6: Specific Vectorized results + Specific Timestamps

For pipes we have interior point result values. These are usually found as vectors with the postfix VEC.

In [40]:
available_result_props=s3s.GetResultProperties_from_elementType(s3s.ObjectTypes.Pipe,False)

In [41]:
available_result_vector_props=[available_result_props for available_result_props in available_result_props if "VEC" in available_result_props]

In [42]:
available_result_vector_props

['HVEC',
 'MVEC',
 'MVECMAX_INST',
 'MVECMIN_INST',
 'PHVEC',
 'PVEC',
 'PVECMAX_INST',
 'PVECMIN_INST',
 'QMVEC',
 'RHOVEC',
 'SVEC',
 'TTRVEC',
 'TVEC',
 'TVECMAX_INST',
 'TVECMIN_INST',
 'ZVEC']

In [51]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["TTRVEC", "MVEC"]
                                        ,timestamps=[0, 5, -2] 
                                        ,use_vector_results=True
                                        )).head(3)

[2025-12-05 20:24:02,651] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2025-12-05 20:24:02,732] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2025-12-05 20:24:02,734] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:24:02,736] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2025-12-05 20:24:02,747] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result properties...
[2025-12-05 20:24:03,775] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 5036)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                           TTRVEC   
interior points                                                                        0    
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.322685           
2023-02-13 05:00:00.000 +01:00                                           0.205774           
2023-02-13 23:00:00.000 +01:00                                           0.303047           

tk                                                                      \
name                                                                     
end_nodes                                                                
property                                                                 
interior points                       1         2         3         4    
timestamp                                                                
2023-02-13 00:00:00.000 +01:00  0.326044  0.329403  0.332762  0.336122   
2023-02-13 05:00:00.000 +01:00  0.207919  0.210064  0.212210  0.214355   
2023-02-13 23:00:00.000 +01:00  0.306203  0.309359  0.312514  0.315670   

tk                                                                      \
name                                                                     
end_nodes                                                                
property                            MVEC                                 
interior points                       0         1         2         3    
timestamp                                                                
2023-02-13 00:00:00.000 +01:00  14.68004  14.68004  14.68004  14.68004   
2023-02-13 05:00:00.000 +01:00  22.98424  22.98424  22.98424  22.98424   
2023-02-13 23:00:00.000 +01:00  15.62682  15.62682  15.62682  15.62682   

tk                                        \
name                                       
end_nodes                                  
property                                   
interior points                       4    
timestamp                                  
2023-02-13 00:00:00.000 +01:00  14.68004   
2023-02-13 05:00:00.000 +01:00  22.98424   
2023-02-13 23:00:00.000 +01:00  15.62682   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                           TTRVEC   
interior points                                                                        0    
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.336122           
2023-02-13 05:00:00.000 +01:00                                           0.214355           
2023-02-13 23:00:00.000 +01:00                                           0.315670           

tk                                                                      \
name                                                                     
end_nodes                                                                
property                                                                 
interior points                       1         2         3         4    
timestamp                                                                
2023-02-13 00:00:00.000 +01:00  0.340352  0.344582  0.348812  0.353042   
2023-02-13 05:00:00.000 +01:00  0.217069  0.219783  0.222497  0.225210   
2

Note that an additional multi index is created that indexes the interior points.

## Merge Metadata and Result Dataframes (for one timestamp)

### Create Dataframes - For pipes

#### Metadata

In [44]:
df_pipes_metadata = s3s.generate_element_metadata_dataframe(element_type=s3s.ObjectTypes.Pipe
                                                            ,properties=["L", "DN"]
                                                            ,geometry=True
                                                            )

[2025-12-05 20:21:26,625] INFO in sir3stoolkit.mantle.dataframes: [metadata] Generating metadata dataframe for element type: ObjectTypes.Pipe
[2025-12-05 20:21:26,627] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:21:26,659] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:21:26,662] INFO in sir3stoolkit.mantle.dataframes: [Resolving Metadata Properties] Using 2 metadata properties.
[2025-12-05 20:21:26,662] INFO in sir3stoolkit.mantle.dataframes: [metadata] Retrieving metadata properties ['L', 'DN'], geometry...
[2025-12-05 20:21:26,830] INFO in sir3stoolkit.mantle.dataframes: [metadata] Transforming DataFrame to GeoDataFrame successful with EPSG: 25832
[2025-12-05 20:21:26,830] INFO in sir3stoolkit.mantle.dataframes: [metadata] Done. Shape: (524, 4)


In [45]:
df_pipes_metadata.head(3)

tk         L   DN  \
0  5442010239090746007  36,42935  150   
1  4917786378639043296  57,21781  125   
2  4762482310382009633  40,99482  125   

                                            geometry  
0  LINESTRING (713620.268 5578828.419, 713602.295...  
1  LINESTRING (713602.295 5578860.106, 713574.062...  
2  LINESTRING (713574.062 5578909.873, 713553.84 ...

#### Results

In [46]:
df_pipes_results = s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                                        ,properties=["DTTR", "PHR"]
                                                        ,timestamps=[0] 
                                                        ,filter_container_tks=[s3s.GetMainContainer()[0]]
                                                        )

[2025-12-05 20:21:26,870] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2025-12-05 20:21:26,947] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] Only static timestamp 2023-02-13 00:00:00.000 +01:00 is used
[2025-12-05 20:21:26,947] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 1 valid timestamp(s) will be used.
[2025-12-05 20:21:26,957] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2025-12-05 20:21:26,992] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] 524 tks remain after container filtering.
[2025-12-05 20:21:26,994] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2025-12-05 20:21:27,002] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result properties...
[2025-12-05 20:21:27,343] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (1, 1048)


In [47]:
df_pipes_results.head(3)

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                            0.02538           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.001812   

tk                                                                    5722206630503885118  \
name                                                                   Rohr V-K43S V-K53S   
end_nodes                      ('4993257270457791438', '5317865645994989592', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.003259           

tk                                        \
name                                       
end_nodes                                  
property     

### Merge

In [48]:
df_pipes_results.columns = df_pipes_results.columns.droplevel([1, 2])
df_pipes_results = df_pipes_results.T.unstack(level=0).T
df_pipes_results = df_pipes_results.droplevel(0, axis=0)
df_pipes = df_pipes_metadata.merge(on="tk",
                    how="outer",
                    right=df_pipes_results)

In [49]:
df_pipes.head(3)

tk         L   DN  \
0  4614463970292122863  7,780674  999   
1  4615723899944629797  64,28724  999   
2  4621030304810285220  3,956838  100   

                                            geometry       DTTR           PHR  
0  LINESTRING (714262.483 5578857.42, 714269.543 ...   7.780674  3.348380e-25  
1  LINESTRING (713738.297 5579219.902, 713793.23 ...  64.287240  3.057601e-24  
2  LINESTRING (713650.613 5578990.488, 713649.498...   0.002291  8.354341e-04